In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import tensorflow as tf
import os, shutil

In [2]:
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.image import ImageDataGenerator

In [3]:
from tensorflow.keras import Sequential
from tensorflow.keras.layers import MaxPooling2D, Conv2D, Flatten, Dense, Dropout
from tensorflow.keras.utils import to_categorical
from keras.preprocessing.image import load_img, img_to_array
from tensorflow.image import central_crop, pad_to_bounding_box, resize

In [4]:
gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
  # Restrict TensorFlow to only allocate 1GB of memory on the first GPU
    try:
        tf.config.experimental.set_virtual_device_configuration(
            gpus[0],
            [tf.config.experimental.VirtualDeviceConfiguration(memory_limit=1024)])
        logical_gpus = tf.config.experimental.list_logical_devices('GPU')
        print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPUs")
    except RuntimeError as e:
        # Virtual devices must be set before GPUs have been initialized
        print(e)

1 Physical GPUs, 1 Logical GPUs


In [5]:
config = tf.compat.v1.ConfigProto()
config.gpu_options.allow_growth = True
config.gpu_options.per_process_gpu_memory_fraction = 0.4 
session = tf.compat.v1.Session(config=config)

In [6]:
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 5565542843140861433
xla_global_id: -1
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 1073741824
locality {
  bus_id: 1
  links {
  }
}
incarnation: 9595328855114016243
physical_device_desc: "device: 0, name: NVIDIA GeForce RTX 2080, pci bus id: 0000:01:00.0, compute capability: 7.5"
xla_global_id: 416903419
]


In [171]:
original_dataset_dir = 'D:\B-Project3\B-Project3\img'

In [172]:
base_dir = 'D:\B-Project3\B-Project3\img_other'

In [173]:
# train data folder

train_dir = os.path.join(base_dir, 'train')
os.mkdir(train_dir)

In [174]:
# validation data foler

validation_dir = os.path.join(base_dir, 'validation')
os.mkdir(validation_dir)

In [175]:
# test data folder

test_dir = os.path.join(base_dir, 'test')
os.mkdir(test_dir)

In [15]:
# train img folder

# train_cats_dir = os.path.join(train_dir, 'Griffith Observatory')
# os.mkdir(train_cats_dir)

['America',
 'Brazil',
 'Germany',
 'Greece',
 'Lebanon',
 'Malaysia',
 'Marrakech',
 'Mexico',
 'Myanmar',
 'Saudi Arabia',
 'Singapore',
 'Spain',
 'Taiwan',
 'United Arab Emirates']

In [176]:
nation_list = os.listdir('img')
nation_list

['America',
 'Australia',
 'Brazil',
 'Cambodia',
 'Chile',
 'China',
 'Czech Republic',
 'Egypt',
 'England',
 'France',
 'Germany',
 'Greece',
 'India',
 'Indonesia',
 'Israel',
 'Italy',
 'Japan',
 'Jordan',
 'Lebanon',
 'Malaysia',
 'Marrakech',
 'Mexico',
 'Myanmar',
 'Peru',
 'Saudi Arabia',
 'Singapore',
 'Spain',
 'Taiwan',
 'Thailand',
 'Turkey',
 'United Arab Emirates']

In [177]:
tour_list = []
for nation in nation_list:
    tour_list.append(os.listdir(f'img/{nation}'))

tour_list

[['Griffith Observatory', 'Statue of Liberty'],
 ['Sydney Opera House'],
 ['Corcovado', 'Escadaria Selaron'],
 ['Angkor Wat'],
 ['Easter Island'],
 ['Canton Tower',
  'Forbidden City',
  'Potala Palace',
  'qin terracotta warriors',
  'The Great Wall'],
 ['Staromestske namesti'],
 ['abu simbel', 'Colossi of Memnon', 'Egypt Pyramid', 'Temple of Karnak'],
 ["St. Paul's Cathedral", 'Stonehenge', 'Tower Bridge'],
 ['Arc de Triomphe',
  'Cathedrale Notre-Dame de Paris',
  'Eiffel Tower',
  'Hotel de Ville',
  'Louvre Museum',
  'Moulin Rouge',
  'Sainte-Chapelle'],
 ['Berliner Dom',
  'Brandenburg Gate',
  'Cologne Cathedral',
  'Hamburg Town Hall',
  'Neuschwanstein',
  'Plonlein'],
 ['Santorini'],
 ['Gateway of India', 'Golden Temple', 'Qutub Minar', 'Taj Mahal'],
 ['Borobudur'],
 ['Tower of David Museum of the History of Jerusalem', 'Western Wall'],
 ['Arco di Costantino',
  'Basilica di San Marco',
  'Bocca della Verita',
  'Campanile di San Marco',
  'Colosseum',
  'Leaning Tower of Pi

In [181]:
tour_li = []

for i in tour_list:
    for j in i:
        tour_li.append(j)
tour_li

['Griffith Observatory',
 'Statue of Liberty',
 'Sydney Opera House',
 'Corcovado',
 'Escadaria Selaron',
 'Angkor Wat',
 'Easter Island',
 'Canton Tower',
 'Forbidden City',
 'Potala Palace',
 'qin terracotta warriors',
 'The Great Wall',
 'Staromestske namesti',
 'abu simbel',
 'Colossi of Memnon',
 'Egypt Pyramid',
 'Temple of Karnak',
 "St. Paul's Cathedral",
 'Stonehenge',
 'Tower Bridge',
 'Arc de Triomphe',
 'Cathedrale Notre-Dame de Paris',
 'Eiffel Tower',
 'Hotel de Ville',
 'Louvre Museum',
 'Moulin Rouge',
 'Sainte-Chapelle',
 'Berliner Dom',
 'Brandenburg Gate',
 'Cologne Cathedral',
 'Hamburg Town Hall',
 'Neuschwanstein',
 'Plonlein',
 'Santorini',
 'Gateway of India',
 'Golden Temple',
 'Qutub Minar',
 'Taj Mahal',
 'Borobudur',
 'Tower of David Museum of the History of Jerusalem',
 'Western Wall',
 'Arco di Costantino',
 'Basilica di San Marco',
 'Bocca della Verita',
 'Campanile di San Marco',
 'Colosseum',
 'Leaning Tower of Pisa',
 'Pantheon',
 'Ponte di Rialto',
 '

In [220]:
for i in tour_li:
    train_tour_dir = os.path.join(train_dir, i)
    os.mkdir(train_tour_dir)


In [231]:
# validation img folder

for i in tour_li:
    validation_tour_dir = os.path.join(validation_dir, i)
    os.mkdir(validation_tour_dir)

In [183]:
# test img folder

for i in tour_li:
    test_tour_dir = os.path.join(test_dir, i)
    os.mkdir(test_tour_dir)

In [185]:
# 관광지별 사진 개수

tour_len = []

for nation in nation_list:
    for tour in tour_li:
        if os.path.exists(f'img/{nation}/{tour}'):
            ab = f'D:\\B-Project3\\B-Project3\\img\\{nation}\\{tour}'
            tour_len.append(len(os.listdir(ab)))
tour_len

[2465,
 2196,
 475,
 133,
 111,
 2399,
 2499,
 2499,
 2495,
 2487,
 175,
 2500,
 2497,
 2497,
 2444,
 2500,
 2500,
 2500,
 2500,
 2500,
 2500,
 2500,
 2500,
 2433,
 2498,
 2468,
 2460,
 2457,
 2500,
 2475,
 2500,
 2500,
 2485,
 2500,
 2452,
 2500,
 2450,
 2500,
 2500,
 2380,
 2500,
 168,
 2418,
 171,
 2431,
 2500,
 2500,
 2500,
 2418,
 2499,
 168,
 2433,
 2500,
 2424,
 2392,
 2500,
 2487,
 2500,
 2466,
 2437,
 2459,
 2500,
 2467,
 2500,
 2500,
 2500,
 148,
 2486,
 1618,
 2500,
 2478,
 2471,
 2500,
 2420,
 2500,
 2500,
 2433,
 2500,
 2433,
 2500]

In [186]:
# 관광지별 사진 40% 개수

tour_four = []

for q in tour_len:
    tour_four.append(int(q * 0.4))

tour_four

[986,
 878,
 190,
 53,
 44,
 959,
 999,
 999,
 998,
 994,
 70,
 1000,
 998,
 998,
 977,
 1000,
 1000,
 1000,
 1000,
 1000,
 1000,
 1000,
 1000,
 973,
 999,
 987,
 984,
 982,
 1000,
 990,
 1000,
 1000,
 994,
 1000,
 980,
 1000,
 980,
 1000,
 1000,
 952,
 1000,
 67,
 967,
 68,
 972,
 1000,
 1000,
 1000,
 967,
 999,
 67,
 973,
 1000,
 969,
 956,
 1000,
 994,
 1000,
 986,
 974,
 983,
 1000,
 986,
 1000,
 1000,
 1000,
 59,
 994,
 647,
 1000,
 991,
 988,
 1000,
 968,
 1000,
 1000,
 973,
 1000,
 973,
 1000]

In [112]:
# 자유의 여신상 파일이름 바꿔주기

file_path = 'D:\B-Project3\B-Project3\img\America\Statue of Liberty'
file_names = os.listdir(file_path)
len(file_names)

2196

In [113]:
i = 0
for name in file_names:
    src = os.path.join(file_path, name)
    dst = str(i) + '.jpg'
    dst = os.path.join(file_path, dst)
    os.rename(src, dst)
    i += 1
    

In [1]:
# 오페라 하우스 파일이름 바꿔주기

file_path = 'D:\B-Project3\B-Project3\img\Australia\Sydney Opera House'
file_names = os.listdir(file_path)
len(file_names)

NameError: name 'os' is not defined

In [117]:
i = 0
for name in file_names:
    src = os.path.join(file_path, name)
    dst = str(i) + '.jpg'
    dst = os.path.join(file_path, dst)
    os.rename(src, dst)
    i += 1

In [121]:
# 브라질 예수상 파일이름 바꿔주기

file_path = 'D:\B-Project3\B-Project3\img\Brazil\Corcovado'
file_names = os.listdir(file_path)
len(file_names)

133

In [122]:
i = 0
for name in file_names:
    src = os.path.join(file_path, name)
    dst = str(i) + '.jpg'
    dst = os.path.join(file_path, dst)
    os.rename(src, dst)
    i += 1

In [132]:
# 앙코와트 파일이름 바꿔주기

file_path = 'D:\B-Project3\B-Project3\img\Cambodia\Angkor Wat'
file_names = os.listdir(file_path)
len(file_names)

2399

In [133]:
i = 0
for name in file_names:
    src = os.path.join(file_path, name)
    dst = str(i) + '.jpg'
    dst = os.path.join(file_path, dst)
    os.rename(src, dst)
    i += 1

In [159]:
# 브라질 계단 파일이름 바꿔주기

file_path = 'D:\B-Project3\B-Project3\img\Brazil\Escadaria Selaron'
file_names = os.listdir(file_path)
len(file_names)

111

In [141]:
i = 0
for name in file_names:
    src = os.path.join(file_path, name)
    dst = str(i) + '.jpg'
    dst = os.path.join(file_path, dst)
    os.rename(src, dst)
    i += 1

In [145]:
# 스페인 카사 바틀로 파일이름 바꿔주기

file_path = 'D:\B-Project3\B-Project3\img\Spain\Casa Batllo'
file_names = os.listdir(file_path)
len(file_names)

148

In [146]:
i = 0
for name in file_names:
    src = os.path.join(file_path, name)
    dst = str(i) + '.jpg'
    dst = os.path.join(file_path, dst)
    os.rename(src, dst)
    i += 1

In [222]:
# train에 관광지별 사진 40% 개수 옮겨주기


fnames = []
for tour_f in tour_four:
    li = ['{}.jpg'.format(j) for j in range(tour_f + 1)]
    fnames.append(li)

for fname in fnames:
    for nation in nation_list:
        for tour in tour_li:
            if os.path.exists(f'img/{nation}/{tour}'):
                if fname in os.listdir(f'D:\B-Project3\B-Project3\img\/{nation}\/{tour}'):
                    print(tour, fname)
                    src = os.path.join(f'D:\B-Project3\B-Project3\img\/{nation}\/{tour}', fname)
                    dst = os.path.join(f'D:\\B-Project3\\B-Project3\\img_other\\train\\{tour}',fname)
                    shutil.copyfile(src, dst)

In [229]:
df = pd.read_excel('data_file/여행지 라벨.xlsx')
datas = df[['en나라', 'en관광지']].values
datas

array([['Greece', 'Santorini'],
       ['Taiwan', 'Taipei 101'],
       ['Taiwan', 'Longshan Temple'],
       ['Germany', 'Neuschwanstein'],
       ['Germany', 'Brandenburg Gate'],
       ['Germany', 'Berliner Dom'],
       ['Germany', 'Hamburg Town Hall'],
       ['Germany', 'Cologne Cathedral'],
       ['Germany', 'Plonlein'],
       ['Lebanon', 'Baalbek'],
       ['Malaysia', 'Petronas Twin Tower'],
       ['Malaysia', 'Khoo Kongsi'],
       ['Mexico', 'Teotihuacan'],
       ['Mexico', 'Chichen Itza'],
       ['Marrakech', 'Koutoubia Mosque'],
       ['America', 'Griffith Observatory'],
       ['America', 'Statue of Liberty'],
       ['Myanmar', 'Ananda Temple'],
       ['Myanmar', 'Shwezigon Paya'],
       ['Myanmar', 'Dhammayangyi Temple'],
       ['Myanmar', 'Shwedagon Pagoda'],
       ['Brazil', 'Corcovado'],
       ['Brazil', 'Escadaria Selaron'],
       ['Saudi Arabia', 'Mecca'],
       ['Spain', 'Sagrada Familia'],
       ['Spain', 'Casa Batllo'],
       ['Spain', 'Parc Guell

In [238]:
path = "D:\B-Project3\B-Project3\\"

for data in datas:
    nation = data[0]
    tour = data[1]
    
    img_num = len(os.listdir(f"img/{nation}/{tour}" ))
    train_num = round(img_num * 0.4)
    validation_num = round(img_num * 0.8)
    test_num = img_num
    
    print(train_num, validation_num - train_num, test_num - validation_num)
    for name in range(train_num):
        src = os.path.join(f'D:\B-Project3\B-Project3\img\/{nation}\/{tour}', f"{name}.jpg")
        dst = os.path.join(f'D:\\B-Project3\\B-Project3\\img_other\\train\\{tour}',f"{name}.jpg")
        shutil.copyfile(src, dst)
        print(f"{tour} {name}.jpg")
    
    for name in range(train_num, validation_num):
        src = os.path.join(f'D:\B-Project3\B-Project3\img\/{nation}\/{tour}', f"{name}.jpg")
        dst = os.path.join(f'D:\\B-Project3\\B-Project3\\img_other\\validation\\{tour}',f"{name}.jpg")
        shutil.copyfile(src, dst)
        print(f"{tour} {name}.jpg")
    
    for name in range(validation_num, test_num):
        src = os.path.join(f'D:\B-Project3\B-Project3\img\/{nation}\/{tour}', f"{name}.jpg")
        dst = os.path.join(f'D:\\B-Project3\\B-Project3\\img_other\\test\\{tour}',f"{name}.jpg")
        shutil.copyfile(src, dst)
        print(f"{tour} {name}.jpg")

1000 1000 500
Santorini 0.jpg
Santorini 1.jpg
Santorini 2.jpg
Santorini 3.jpg
Santorini 4.jpg
Santorini 5.jpg
Santorini 6.jpg
Santorini 7.jpg
Santorini 8.jpg
Santorini 9.jpg
Santorini 10.jpg
Santorini 11.jpg
Santorini 12.jpg
Santorini 13.jpg
Santorini 14.jpg
Santorini 15.jpg
Santorini 16.jpg
Santorini 17.jpg
Santorini 18.jpg
Santorini 19.jpg
Santorini 20.jpg
Santorini 21.jpg
Santorini 22.jpg
Santorini 23.jpg
Santorini 24.jpg
Santorini 25.jpg
Santorini 26.jpg
Santorini 27.jpg
Santorini 28.jpg
Santorini 29.jpg
Santorini 30.jpg
Santorini 31.jpg
Santorini 32.jpg
Santorini 33.jpg
Santorini 34.jpg
Santorini 35.jpg
Santorini 36.jpg
Santorini 37.jpg
Santorini 38.jpg
Santorini 39.jpg
Santorini 40.jpg
Santorini 41.jpg
Santorini 42.jpg
Santorini 43.jpg
Santorini 44.jpg
Santorini 45.jpg
Santorini 46.jpg
Santorini 47.jpg
Santorini 48.jpg
Santorini 49.jpg
Santorini 50.jpg
Santorini 51.jpg
Santorini 52.jpg
Santorini 53.jpg
Santorini 54.jpg
Santorini 55.jpg
Santorini 56.jpg
Santorini 57.jpg
Santorini 

Santorini 565.jpg
Santorini 566.jpg
Santorini 567.jpg
Santorini 568.jpg
Santorini 569.jpg
Santorini 570.jpg
Santorini 571.jpg
Santorini 572.jpg
Santorini 573.jpg
Santorini 574.jpg
Santorini 575.jpg
Santorini 576.jpg
Santorini 577.jpg
Santorini 578.jpg
Santorini 579.jpg
Santorini 580.jpg
Santorini 581.jpg
Santorini 582.jpg
Santorini 583.jpg
Santorini 584.jpg
Santorini 585.jpg
Santorini 586.jpg
Santorini 587.jpg
Santorini 588.jpg
Santorini 589.jpg
Santorini 590.jpg
Santorini 591.jpg
Santorini 592.jpg
Santorini 593.jpg
Santorini 594.jpg
Santorini 595.jpg
Santorini 596.jpg
Santorini 597.jpg
Santorini 598.jpg
Santorini 599.jpg
Santorini 600.jpg
Santorini 601.jpg
Santorini 602.jpg
Santorini 603.jpg
Santorini 604.jpg
Santorini 605.jpg
Santorini 606.jpg
Santorini 607.jpg
Santorini 608.jpg
Santorini 609.jpg
Santorini 610.jpg
Santorini 611.jpg
Santorini 612.jpg
Santorini 613.jpg
Santorini 614.jpg
Santorini 615.jpg
Santorini 616.jpg
Santorini 617.jpg
Santorini 618.jpg
Santorini 619.jpg
Santorini 

Santorini 1148.jpg
Santorini 1149.jpg
Santorini 1150.jpg
Santorini 1151.jpg
Santorini 1152.jpg
Santorini 1153.jpg
Santorini 1154.jpg
Santorini 1155.jpg
Santorini 1156.jpg
Santorini 1157.jpg
Santorini 1158.jpg
Santorini 1159.jpg
Santorini 1160.jpg
Santorini 1161.jpg
Santorini 1162.jpg
Santorini 1163.jpg
Santorini 1164.jpg
Santorini 1165.jpg
Santorini 1166.jpg
Santorini 1167.jpg
Santorini 1168.jpg
Santorini 1169.jpg
Santorini 1170.jpg
Santorini 1171.jpg
Santorini 1172.jpg
Santorini 1173.jpg
Santorini 1174.jpg
Santorini 1175.jpg
Santorini 1176.jpg
Santorini 1177.jpg
Santorini 1178.jpg
Santorini 1179.jpg
Santorini 1180.jpg
Santorini 1181.jpg
Santorini 1182.jpg
Santorini 1183.jpg
Santorini 1184.jpg
Santorini 1185.jpg
Santorini 1186.jpg
Santorini 1187.jpg
Santorini 1188.jpg
Santorini 1189.jpg
Santorini 1190.jpg
Santorini 1191.jpg
Santorini 1192.jpg
Santorini 1193.jpg
Santorini 1194.jpg
Santorini 1195.jpg
Santorini 1196.jpg
Santorini 1197.jpg
Santorini 1198.jpg
Santorini 1199.jpg
Santorini 12

Santorini 1668.jpg
Santorini 1669.jpg
Santorini 1670.jpg
Santorini 1671.jpg
Santorini 1672.jpg
Santorini 1673.jpg
Santorini 1674.jpg
Santorini 1675.jpg
Santorini 1676.jpg
Santorini 1677.jpg
Santorini 1678.jpg
Santorini 1679.jpg
Santorini 1680.jpg
Santorini 1681.jpg
Santorini 1682.jpg
Santorini 1683.jpg
Santorini 1684.jpg
Santorini 1685.jpg
Santorini 1686.jpg
Santorini 1687.jpg
Santorini 1688.jpg
Santorini 1689.jpg
Santorini 1690.jpg
Santorini 1691.jpg
Santorini 1692.jpg
Santorini 1693.jpg
Santorini 1694.jpg
Santorini 1695.jpg
Santorini 1696.jpg
Santorini 1697.jpg
Santorini 1698.jpg
Santorini 1699.jpg
Santorini 1700.jpg
Santorini 1701.jpg
Santorini 1702.jpg
Santorini 1703.jpg
Santorini 1704.jpg
Santorini 1705.jpg
Santorini 1706.jpg
Santorini 1707.jpg
Santorini 1708.jpg
Santorini 1709.jpg
Santorini 1710.jpg
Santorini 1711.jpg
Santorini 1712.jpg
Santorini 1713.jpg
Santorini 1714.jpg
Santorini 1715.jpg
Santorini 1716.jpg
Santorini 1717.jpg
Santorini 1718.jpg
Santorini 1719.jpg
Santorini 17

Santorini 2208.jpg
Santorini 2209.jpg
Santorini 2210.jpg
Santorini 2211.jpg
Santorini 2212.jpg
Santorini 2213.jpg
Santorini 2214.jpg
Santorini 2215.jpg
Santorini 2216.jpg
Santorini 2217.jpg
Santorini 2218.jpg
Santorini 2219.jpg
Santorini 2220.jpg
Santorini 2221.jpg
Santorini 2222.jpg
Santorini 2223.jpg
Santorini 2224.jpg
Santorini 2225.jpg
Santorini 2226.jpg
Santorini 2227.jpg
Santorini 2228.jpg
Santorini 2229.jpg
Santorini 2230.jpg
Santorini 2231.jpg
Santorini 2232.jpg
Santorini 2233.jpg
Santorini 2234.jpg
Santorini 2235.jpg
Santorini 2236.jpg
Santorini 2237.jpg
Santorini 2238.jpg
Santorini 2239.jpg
Santorini 2240.jpg
Santorini 2241.jpg
Santorini 2242.jpg
Santorini 2243.jpg
Santorini 2244.jpg
Santorini 2245.jpg
Santorini 2246.jpg
Santorini 2247.jpg
Santorini 2248.jpg
Santorini 2249.jpg
Santorini 2250.jpg
Santorini 2251.jpg
Santorini 2252.jpg
Santorini 2253.jpg
Santorini 2254.jpg
Santorini 2255.jpg
Santorini 2256.jpg
Santorini 2257.jpg
Santorini 2258.jpg
Santorini 2259.jpg
Santorini 22

...

Hotel de Ville 1317.jpg
Hotel de Ville 1318.jpg
Hotel de Ville 1319.jpg
Hotel de Ville 1320.jpg
Hotel de Ville 1321.jpg
Hotel de Ville 1322.jpg
Hotel de Ville 1323.jpg
Hotel de Ville 1324.jpg
Hotel de Ville 1325.jpg
Hotel de Ville 1326.jpg
Hotel de Ville 1327.jpg
Hotel de Ville 1328.jpg
Hotel de Ville 1329.jpg
Hotel de Ville 1330.jpg
Hotel de Ville 1331.jpg
Hotel de Ville 1332.jpg
Hotel de Ville 1333.jpg
Hotel de Ville 1334.jpg
Hotel de Ville 1335.jpg
Hotel de Ville 1336.jpg
Hotel de Ville 1337.jpg
Hotel de Ville 1338.jpg
Hotel de Ville 1339.jpg
Hotel de Ville 1340.jpg
Hotel de Ville 1341.jpg
Hotel de Ville 1342.jpg
Hotel de Ville 1343.jpg
Hotel de Ville 1344.jpg
Hotel de Ville 1345.jpg
Hotel de Ville 1346.jpg
Hotel de Ville 1347.jpg
Hotel de Ville 1348.jpg
Hotel de Ville 1349.jpg
Hotel de Ville 1350.jpg
Hotel de Ville 1351.jpg
Hotel de Ville 1352.jpg
Hotel de Ville 1353.jpg
Hotel de Ville 1354.jpg
Hotel de Ville 1355.jpg
Hotel de Ville 1356.jpg
Hotel de Ville 1357.jpg
Hotel de Ville 1

Hotel de Ville 1663.jpg
Hotel de Ville 1664.jpg
Hotel de Ville 1665.jpg
Hotel de Ville 1666.jpg
Hotel de Ville 1667.jpg
Hotel de Ville 1668.jpg
Hotel de Ville 1669.jpg
Hotel de Ville 1670.jpg
Hotel de Ville 1671.jpg
Hotel de Ville 1672.jpg
Hotel de Ville 1673.jpg
Hotel de Ville 1674.jpg
Hotel de Ville 1675.jpg
Hotel de Ville 1676.jpg
Hotel de Ville 1677.jpg
Hotel de Ville 1678.jpg
Hotel de Ville 1679.jpg
Hotel de Ville 1680.jpg
Hotel de Ville 1681.jpg
Hotel de Ville 1682.jpg
Hotel de Ville 1683.jpg
Hotel de Ville 1684.jpg
Hotel de Ville 1685.jpg
Hotel de Ville 1686.jpg
Hotel de Ville 1687.jpg
Hotel de Ville 1688.jpg
Hotel de Ville 1689.jpg
Hotel de Ville 1690.jpg
Hotel de Ville 1691.jpg
Hotel de Ville 1692.jpg
Hotel de Ville 1693.jpg
Hotel de Ville 1694.jpg
Hotel de Ville 1695.jpg
Hotel de Ville 1696.jpg
Hotel de Ville 1697.jpg
Hotel de Ville 1698.jpg
Hotel de Ville 1699.jpg
Hotel de Ville 1700.jpg
Hotel de Ville 1701.jpg
Hotel de Ville 1702.jpg
Hotel de Ville 1703.jpg
Hotel de Ville 1

Hotel de Ville 2034.jpg
Hotel de Ville 2035.jpg
Hotel de Ville 2036.jpg
Hotel de Ville 2037.jpg
Hotel de Ville 2038.jpg
Hotel de Ville 2039.jpg
Hotel de Ville 2040.jpg
Hotel de Ville 2041.jpg
Hotel de Ville 2042.jpg
Hotel de Ville 2043.jpg
Hotel de Ville 2044.jpg
Hotel de Ville 2045.jpg
Hotel de Ville 2046.jpg
Hotel de Ville 2047.jpg
Hotel de Ville 2048.jpg
Hotel de Ville 2049.jpg
Hotel de Ville 2050.jpg
Hotel de Ville 2051.jpg
Hotel de Ville 2052.jpg
Hotel de Ville 2053.jpg
Hotel de Ville 2054.jpg
Hotel de Ville 2055.jpg
Hotel de Ville 2056.jpg
Hotel de Ville 2057.jpg
Hotel de Ville 2058.jpg
Hotel de Ville 2059.jpg
Hotel de Ville 2060.jpg
Hotel de Ville 2061.jpg
Hotel de Ville 2062.jpg
Hotel de Ville 2063.jpg
Hotel de Ville 2064.jpg
Hotel de Ville 2065.jpg
Hotel de Ville 2066.jpg
Hotel de Ville 2067.jpg
Hotel de Ville 2068.jpg
Hotel de Ville 2069.jpg
Hotel de Ville 2070.jpg
Hotel de Ville 2071.jpg
Hotel de Ville 2072.jpg
Hotel de Ville 2073.jpg
Hotel de Ville 2074.jpg
Hotel de Ville 2

Hotel de Ville 2390.jpg
Hotel de Ville 2391.jpg
Hotel de Ville 2392.jpg
Hotel de Ville 2393.jpg
Hotel de Ville 2394.jpg
Hotel de Ville 2395.jpg
Hotel de Ville 2396.jpg
Hotel de Ville 2397.jpg
Hotel de Ville 2398.jpg
Hotel de Ville 2399.jpg
Hotel de Ville 2400.jpg
Hotel de Ville 2401.jpg
Hotel de Ville 2402.jpg
Hotel de Ville 2403.jpg
Hotel de Ville 2404.jpg
Hotel de Ville 2405.jpg
Hotel de Ville 2406.jpg
Hotel de Ville 2407.jpg
Hotel de Ville 2408.jpg
Hotel de Ville 2409.jpg
Hotel de Ville 2410.jpg
Hotel de Ville 2411.jpg
Hotel de Ville 2412.jpg
Hotel de Ville 2413.jpg
Hotel de Ville 2414.jpg
Hotel de Ville 2415.jpg
Hotel de Ville 2416.jpg
Hotel de Ville 2417.jpg
Hotel de Ville 2418.jpg
Hotel de Ville 2419.jpg
Hotel de Ville 2420.jpg
Hotel de Ville 2421.jpg
Hotel de Ville 2422.jpg
Hotel de Ville 2423.jpg
Hotel de Ville 2424.jpg
Hotel de Ville 2425.jpg
Hotel de Ville 2426.jpg
Hotel de Ville 2427.jpg
Hotel de Ville 2428.jpg
Hotel de Ville 2429.jpg
Hotel de Ville 2430.jpg
Hotel de Ville 2

Sydney Opera House 270.jpg
Sydney Opera House 271.jpg
Sydney Opera House 272.jpg
Sydney Opera House 273.jpg
Sydney Opera House 274.jpg
Sydney Opera House 275.jpg
Sydney Opera House 276.jpg
Sydney Opera House 277.jpg
Sydney Opera House 278.jpg
Sydney Opera House 279.jpg
Sydney Opera House 280.jpg
Sydney Opera House 281.jpg
Sydney Opera House 282.jpg
Sydney Opera House 283.jpg
Sydney Opera House 284.jpg
Sydney Opera House 285.jpg
Sydney Opera House 286.jpg
Sydney Opera House 287.jpg
Sydney Opera House 288.jpg
Sydney Opera House 289.jpg
Sydney Opera House 290.jpg
Sydney Opera House 291.jpg
Sydney Opera House 292.jpg
Sydney Opera House 293.jpg
Sydney Opera House 294.jpg
Sydney Opera House 295.jpg
Sydney Opera House 296.jpg
Sydney Opera House 297.jpg
Sydney Opera House 298.jpg
Sydney Opera House 299.jpg
Sydney Opera House 300.jpg
Sydney Opera House 301.jpg
Sydney Opera House 302.jpg
Sydney Opera House 303.jpg
Sydney Opera House 304.jpg
Sydney Opera House 305.jpg
Sydney Opera House 306.jpg
S

In [211]:
# validation에 관광지별 사진 40% 개수 옮겨주기

fnames = []
for tour_f in tour_four:
    li = ['{}.jpg'.format(j) for j in range(tour_f)]
    fnames.append(li)

for fname in fnames:
    for nation in nation_list:
        for tour in tour_li:
            for f in fname:
                if os.path.exists(f'img/{nation}/{tour}'):
                    #for fname in os.listdir(f'D:\B-Project3\B-Project3\img\/{nation}\/{tour}'):
                        print(tour, f)
                        src = os.path.join(f'D:\B-Project3\B-Project3\img\/{nation}\/{tour}', f)
                        dst = os.path.join(f'D:\\B-Project3\\B-Project3\\img_other\\validation\\{tour}',f)
                        shutil.copyfile(src, dst)

Griffith Observatory 0.jpg
Griffith Observatory 1.jpg
Griffith Observatory 2.jpg
Griffith Observatory 3.jpg
Griffith Observatory 4.jpg
Griffith Observatory 5.jpg
Griffith Observatory 6.jpg
Griffith Observatory 7.jpg
Griffith Observatory 8.jpg
Griffith Observatory 9.jpg
Griffith Observatory 10.jpg
Griffith Observatory 11.jpg
Griffith Observatory 12.jpg
Griffith Observatory 13.jpg
Griffith Observatory 14.jpg
Griffith Observatory 15.jpg
Griffith Observatory 16.jpg
Griffith Observatory 17.jpg
Griffith Observatory 18.jpg
Griffith Observatory 19.jpg
Griffith Observatory 20.jpg
Griffith Observatory 21.jpg
Griffith Observatory 22.jpg
Griffith Observatory 23.jpg
Griffith Observatory 24.jpg
Griffith Observatory 25.jpg
Griffith Observatory 26.jpg
Griffith Observatory 27.jpg
Griffith Observatory 28.jpg
Griffith Observatory 29.jpg
Griffith Observatory 30.jpg
Griffith Observatory 31.jpg
Griffith Observatory 32.jpg
Griffith Observatory 33.jpg
Griffith Observatory 34.jpg
Griffith Observatory 35.jpg
Gr

Griffith Observatory 401.jpg
Griffith Observatory 402.jpg
Griffith Observatory 403.jpg
Griffith Observatory 404.jpg
Griffith Observatory 405.jpg
Griffith Observatory 406.jpg
Griffith Observatory 407.jpg
Griffith Observatory 408.jpg
Griffith Observatory 409.jpg
Griffith Observatory 410.jpg
Griffith Observatory 411.jpg
Griffith Observatory 412.jpg
Griffith Observatory 413.jpg
Griffith Observatory 414.jpg
Griffith Observatory 415.jpg
Griffith Observatory 416.jpg
Griffith Observatory 417.jpg
Griffith Observatory 418.jpg
Griffith Observatory 419.jpg
Griffith Observatory 420.jpg
Griffith Observatory 421.jpg
Griffith Observatory 422.jpg
Griffith Observatory 423.jpg
Griffith Observatory 424.jpg
Griffith Observatory 425.jpg
Griffith Observatory 426.jpg
Griffith Observatory 427.jpg
Griffith Observatory 428.jpg
Griffith Observatory 429.jpg
Griffith Observatory 430.jpg
Griffith Observatory 431.jpg
Griffith Observatory 432.jpg
Griffith Observatory 433.jpg
Griffith Observatory 434.jpg
Griffith Obser

Griffith Observatory 838.jpg
Griffith Observatory 839.jpg
Griffith Observatory 840.jpg
Griffith Observatory 841.jpg
Griffith Observatory 842.jpg
Griffith Observatory 843.jpg
Griffith Observatory 844.jpg
Griffith Observatory 845.jpg
Griffith Observatory 846.jpg
Griffith Observatory 847.jpg
Griffith Observatory 848.jpg
Griffith Observatory 849.jpg
Griffith Observatory 850.jpg
Griffith Observatory 851.jpg
Griffith Observatory 852.jpg
Griffith Observatory 853.jpg
Griffith Observatory 854.jpg
Griffith Observatory 855.jpg
Griffith Observatory 856.jpg
Griffith Observatory 857.jpg
Griffith Observatory 858.jpg
Griffith Observatory 859.jpg
Griffith Observatory 860.jpg
Griffith Observatory 861.jpg
Griffith Observatory 862.jpg
Griffith Observatory 863.jpg
Griffith Observatory 864.jpg
Griffith Observatory 865.jpg
Griffith Observatory 866.jpg
Griffith Observatory 867.jpg
Griffith Observatory 868.jpg
Griffith Observatory 869.jpg
Griffith Observatory 870.jpg
Griffith Observatory 871.jpg
Griffith Obser

Statue of Liberty 294.jpg
Statue of Liberty 295.jpg
Statue of Liberty 296.jpg
Statue of Liberty 297.jpg
Statue of Liberty 298.jpg
Statue of Liberty 299.jpg
Statue of Liberty 300.jpg
Statue of Liberty 301.jpg
Statue of Liberty 302.jpg
Statue of Liberty 303.jpg
Statue of Liberty 304.jpg
Statue of Liberty 305.jpg
Statue of Liberty 306.jpg
Statue of Liberty 307.jpg
Statue of Liberty 308.jpg
Statue of Liberty 309.jpg
Statue of Liberty 310.jpg
Statue of Liberty 311.jpg
Statue of Liberty 312.jpg
Statue of Liberty 313.jpg
Statue of Liberty 314.jpg
Statue of Liberty 315.jpg
Statue of Liberty 316.jpg
Statue of Liberty 317.jpg
Statue of Liberty 318.jpg
Statue of Liberty 319.jpg
Statue of Liberty 320.jpg
Statue of Liberty 321.jpg
Statue of Liberty 322.jpg
Statue of Liberty 323.jpg
Statue of Liberty 324.jpg
Statue of Liberty 325.jpg
Statue of Liberty 326.jpg
Statue of Liberty 327.jpg
Statue of Liberty 328.jpg
Statue of Liberty 329.jpg
Statue of Liberty 330.jpg
Statue of Liberty 331.jpg
Statue of Li

Statue of Liberty 735.jpg
Statue of Liberty 736.jpg
Statue of Liberty 737.jpg
Statue of Liberty 738.jpg
Statue of Liberty 739.jpg
Statue of Liberty 740.jpg
Statue of Liberty 741.jpg
Statue of Liberty 742.jpg
Statue of Liberty 743.jpg
Statue of Liberty 744.jpg
Statue of Liberty 745.jpg
Statue of Liberty 746.jpg
Statue of Liberty 747.jpg
Statue of Liberty 748.jpg
Statue of Liberty 749.jpg
Statue of Liberty 750.jpg
Statue of Liberty 751.jpg
Statue of Liberty 752.jpg
Statue of Liberty 753.jpg
Statue of Liberty 754.jpg
Statue of Liberty 755.jpg
Statue of Liberty 756.jpg
Statue of Liberty 757.jpg
Statue of Liberty 758.jpg
Statue of Liberty 759.jpg
Statue of Liberty 760.jpg
Statue of Liberty 761.jpg
Statue of Liberty 762.jpg
Statue of Liberty 763.jpg
Statue of Liberty 764.jpg
Statue of Liberty 765.jpg
Statue of Liberty 766.jpg
Statue of Liberty 767.jpg
Statue of Liberty 768.jpg
Statue of Liberty 769.jpg
Statue of Liberty 770.jpg
Statue of Liberty 771.jpg
Statue of Liberty 772.jpg
Statue of Li

Sydney Opera House 361.jpg
Sydney Opera House 362.jpg
Sydney Opera House 363.jpg
Sydney Opera House 364.jpg
Sydney Opera House 365.jpg
Sydney Opera House 366.jpg
Sydney Opera House 367.jpg
Sydney Opera House 368.jpg
Sydney Opera House 369.jpg
Sydney Opera House 370.jpg
Sydney Opera House 371.jpg
Sydney Opera House 372.jpg
Sydney Opera House 373.jpg
Sydney Opera House 374.jpg
Sydney Opera House 375.jpg
Sydney Opera House 376.jpg
Sydney Opera House 377.jpg
Sydney Opera House 378.jpg
Sydney Opera House 379.jpg
Sydney Opera House 380.jpg
Sydney Opera House 381.jpg
Sydney Opera House 382.jpg
Sydney Opera House 383.jpg
Sydney Opera House 384.jpg
Sydney Opera House 385.jpg
Sydney Opera House 386.jpg
Sydney Opera House 387.jpg
Sydney Opera House 388.jpg
Sydney Opera House 389.jpg
Sydney Opera House 390.jpg
Sydney Opera House 391.jpg
Sydney Opera House 392.jpg
Sydney Opera House 393.jpg
Sydney Opera House 394.jpg
Sydney Opera House 395.jpg
Sydney Opera House 396.jpg
Sydney Opera House 397.jpg
S

FileNotFoundError: [Errno 2] No such file or directory: 'D:\\B-Project3\\B-Project3\\img\\/Australia\\/Sydney Opera House\\475.jpg'

In [1]:
36864*3

110592